In [2]:
# import the library
import googlemaps
import json
import pprint
import xlsxwriter
import time
import pandas as pd
import os
from datetime import datetime
import sqlite3
os.chdir('/Users/oanottage/Desktop/BTS/Data Science Foundations/DSFinal/')

import configparser
config = configparser.ConfigParser()
config.read('secrets/config.ini')


# Define the Client
gmaps = googlemaps.Client(key = config['DEFAULT']['google_api_key'])

In [2]:
categories = ['accounting', 'airport', 'amusement_park', 'aquarium', 'art_gallery', 'atm', 'bakery', 'bank', 'bar', 'beauty_salon', 'bicycle_store', 'book_store', 'bowling_alley', 'bus_station', 'cafe', 'campground', 'car_dealer', 'car_rental', 'car_repair', 'car_wash', 'casino', 'cemetery', 'church', 'city_hall', 'clothing_store', 'convenience_store', 'courthouse', 'dentist', 'department_store', 'doctor', 'drugstore', 'electrician', 'electronics_store', 'embassy', 'fire_station', 'florist', 'funeral_home', 'furniture_store', 'gas_station', 'gym', 'hair_care', 'hardware_store', 'hindu_temple', 'home_goods_store', 'hospital', 'insurance_agency', 'jewelry_store', 'laundry', 'lawyer', 'library', 'light_rail_station', 'liquor_store', 'local_government_office', 'locksmith', 'lodging', 'meal_delivery', 'meal_takeaway', 'mosque', 'movie_rental', 'movie_theater', 'moving_company', 'museum', 'night_club', 'painter', 'park', 'parking', 'pet_store', 'pharmacy', 'physiotherapist', 'plumber', 'police', 'post_office', 'primary_school', 'real_estate_agency', 'restaurant', 'roofing_contractor', 'rv_park', 'school', 'secondary_school', 'shoe_store', 'shopping_mall', 'spa', 'stadium', 'storage', 'store', 'subway_station', 'supermarket', 'synagogue', 'taxi_stand', 'tourist_attraction', 'train_station', 'transit_station', 'travel_agency', 'university', 'veterinary_care', 'zoo']


In [3]:
stored_results = []

for category in categories:
    try:
        places_result  = gmaps.places_nearby(location='41.397447, 2.164331', radius = 50000 , type = str(category))
        for _ in range(150):
            # loop through each of the places in the results, and get the place details.      
            for place in places_result['results']:

                # define the place id, needed to get place details. Formatted as a string.
                my_place_id = place['place_id']

                # define the fields you would liked return. Formatted as a list.
                my_fields = ['place_id','url','name','formatted_phone_number','international_phone_number','type','rating','user_ratings_total','geometry/location/lng','geometry/location/lat','website', 'opening_hours', 'price_level','business_status','permanently_closed']

                # make a request for the details.
                places_details  = gmaps.place(place_id= my_place_id , fields= my_fields)

                

                print('---------------')

                # store the results in a list object.
                stored_results.append({'category':category})
                stored_results.append(places_details['result'])   
                
                # print the results of the details, returned as a dictionary.
                pprint.pprint({'category':category})
                pprint.pprint(places_details['result'])

            time.sleep(3)    
            pprint.pprint(places_result['next_page_token'])
            places_result  = gmaps.places_nearby(page_token = places_result['next_page_token'])
            print('===================')
    except:
        continue

---------------
{'category': 'accounting'}
{'business_status': 'OPERATIONAL',
 'formatted_phone_number': '912 24 94 26',
 'geometry': {'location': {'lat': 41.3905719, 'lng': 2.166376899999999}},
 'international_phone_number': '+34 912 24 94 26',
 'name': 'BBVA',
 'opening_hours': {'open_now': True,
                   'periods': [{'close': {'day': 1, 'time': '1415'},
                                'open': {'day': 1, 'time': '0830'}},
                               {'close': {'day': 2, 'time': '1415'},
                                'open': {'day': 2, 'time': '0830'}},
                               {'close': {'day': 3, 'time': '1415'},
                                'open': {'day': 3, 'time': '0830'}},
                               {'close': {'day': 4, 'time': '1415'},
                                'open': {'day': 4, 'time': '0830'}},
                               {'close': {'day': 5, 'time': '1415'},
                                'open': {'day': 5, 'time': '0830'}}],
         

In [4]:
len(stored_results)

7038

In [5]:
# Convert the lead list into a Pandas DataFrame
raw = pd.DataFrame(stored_results)
raw['category'] = raw['category'].shift(1)

In [6]:
df = raw.copy()

In [7]:
df = df.dropna(how='all')

In [8]:
df = df.reset_index(drop=True)

In [9]:
df['coordinates'] = df['geometry'].apply(lambda x: x['location'])
df['latitude'] = df['coordinates'].apply(lambda x: x['lat'])
df['longitude'] = df['coordinates'].apply(lambda x: x['lng'])

In [10]:
df.drop(columns=['geometry','coordinates'], inplace=True)

In [11]:
df

category business_status formatted_phone_number  \
0          accounting     OPERATIONAL           912 24 94 26   
1          accounting     OPERATIONAL           934 67 70 21   
2          accounting     OPERATIONAL           932 45 88 07   
3          accounting     OPERATIONAL           933 17 29 75   
4          accounting     OPERATIONAL           932 72 14 11   
...               ...             ...                    ...   
3514  veterinary_care     OPERATIONAL           637 84 43 98   
3515  veterinary_care     OPERATIONAL           933 23 54 44   
3516  veterinary_care     OPERATIONAL           934 12 59 44   
3517  veterinary_care     OPERATIONAL           696 65 57 20   
3518  veterinary_care     OPERATIONAL           937 07 02 49   

     international_phone_number                            name  \
0              +34 912 24 94 26                            BBVA   
1              +34 934 67 70 21                            BBVA   
2              +34 932 45 88 07               Oficina Banc BBVA   
3              +34 933 17 29 75                ADD Work Systems   
4              +34 932 72 14 11                     Acordia ACR   
...                         ...                             ...   
3514           +34 637 84 43 98  Clínica Veterinària Family Vet   
3515           +34 933 23 54 44         Tot Cat. Clínica felina   
3516           +34 934 12 59 44                 Vet & Stil Casp   
3517           +34 696 65 57 20      CENTRE VETERINARI HOLÍSTIC   
3518           +34 937 07 02 49    Hospital Veterinari Provença   

                                          opening_hours  \
0     {'open_now': True, 'periods': [{'close': {'day...   
1     {'open_now': True, 'periods': [{'close': {'day...   
2     {'open_now': True, 'periods': [{'close': {'day...   
3     {'open_now': True, 'periods': [{'close': {'day...   
4     {'open_now': True, 'periods': [{'close': {'day...   
...                                                 ...   
3514  {'open_now': True, 'periods': [{'close': {'day...   
3515  {'open_now': False, 'periods': [{'close': {'da...   
3516  {'open_now': True, 'periods': [{'close': {'day...   
3517  {'open_now': True, 'periods': [{'close': {'day...   
3518  {'open_now': True, 'periods': [{'open': {'day'...   

                         place_id  rating  \
0     ChIJC4wKC5OipBIRNylnuSiqc8g     2.4   
1     ChIJTcKWdeqipBIRYcZ6mcS-5ak     2.0   
2     ChIJG5hR4eWipBIR0NaV1YhuB8g     2.1   
3     ChIJ01Y_O_CipBIR6u330Kjcw_o     NaN   
4     ChIJC_7JOJOipBIRz09nzVB5h_U     2.7   
...                           ...     ...   
3514  ChIJyx0ZczyjpBIRgq1Jge2aNj4     4.9   
3515  ChIJozbbxI-ipBIRJRY_zyv1rgs     4.6   
3516  ChIJ__-P6e-ipBIRXRlQ5NPijlw     4.8   
3517  ChIJj3S--GWjpBIREgmNvK1kMrc     4.8   
3518  ChIJ9dnj54-ipBIRCBUoVjIQLjw     3.9   

                                                  types  \
0     [bank, atm, accounting, finance, point_of_inte...   
1     [bank, atm, accounting, finance, point_of_inte...   
2     [bank, atm, accounting, finance, point_of_inte...   
3     [accounting, finance, point_of_interest, estab...   
4     [accounting, finance, point_of_interest, estab...   
...                                                 ...   
3514  [veterinary_care, point_of_interest, establish...   
3515  [veterinary_care, point_of_interest, establish...   
3516  [veterinary_care, point_of_interest, establish...   
3517  [veterinary_care, point_of_interest, establish...   
3518  [pharmacy, veterinary_care, store, food, point...   

                                                    url  user_ratings_total  \
0     https://maps.google.com/?cid=14444075521793272119                82.0   
1     https://maps.google.com/?cid=12242400913674389089                42.0   
2     https://maps.google.com/?cid=14413610666400536272                46.0   
3     https://maps.google.com/?cid=18069528747559087594                 NaN   
4     https://maps.google.com/?cid=17692243049098727375                 3.0   
...   

In [13]:
today = datetime.today().date()

In [16]:
df.to_csv(f'data/external/Google/lead_list_barcelona_{today}.csv',index=False)

In [ ]:
df['TimeStamp'] = today

In [2]:
#Run the 'create if it doesn't exist' SQL statement
def create_db(folder,table_name, df):
    # Open a connection to the database and create a cursor
    cnx = sqlite3.connect(f'{folder}/DSFinal.db')
    c = cnx.cursor()

    # Get the column names and types from the dataframe
    cols = df.columns.tolist()
    types = df.dtypes.tolist()

    # Create the SQL CREATE TABLE statement
    create_statement = f"CREATE TABLE IF NOT EXISTS {table_name}({', '.join([f'{col} {type}' for col, type in zip(cols, types)])})"

    # Execute the CREATE TABLE statement
    c.execute(create_statement)

    # Commit the changes and close the cursor and connection
    cnx.commit()



#Creating the table
def create_table(folder,table_name, df):
    cnx = sqlite3.connect(f'{folder}/DSFinal.db')
    c = cnx.cursor()
    # Get the list of column names and data types in the DataFrame
    cols = list(df.columns)
    types = df.dtypes.apply(lambda x: x.name).tolist()
    
    # Create the CREATE TABLE statement dynamically
    create_statement = f"CREATE TABLE IF NOT EXISTS {table_name}({', '.join([f'{col} {type.upper()}' for col, type in zip(cols, types)])})"
    
    # Execute the CREATE TABLE statement
    c.execute(create_statement)
    # Commit the changes and close the cursor and connection
    cnx.commit()



#Dynamic Insertion
def dynamic_insertion(folder,table_name, df):
    cnx = sqlite3.connect(f'{folder}/DSFinal.db')
    c = cnx.cursor()
    # Get the list of column names in the DataFrame
    cols = list(df.columns)
    
    # Create the INSERT statement dynamically
    insert_statement = f"INSERT INTO {table_name}({', '.join(cols)}) VALUES ({', '.join(['?' for _ in range(len(cols))])})"
    
    # Insert the data into the database
    for index, row in df.iterrows():
        c.execute(insert_statement, tuple(row))
        cnx.commit()
    
    # Close the database connection and cursor
    c.close()
    cnx.close()

#Putting it all together
def push(folder,table_name, df):
  create_db(folder,table_name, df)
  create_table(folder,table_name,df)
  dynamic_insertion(folder,table_name,df)

In [ ]:
push('databases','gmaps_lead_list',df)
push('deliverables','gmaps_lead_list',df)